## Importing our libraries

In [1]:
# NeMo's "core" package
import nemo
import librosa
import os
import sys
import os
import pandas as pd
import subprocess
import json
import codecs
import pyarabic.araby as araby
import soundfile as sf
import pytorch_lightning as pl
from pytorch_lightning.strategies import *
import IPython.display as ipd
import nemo.collections.asr as nemo_asr
from nemo.utils.exp_manager import exp_manager
from IPython.display import Javascript
from base64 import b64decode
from omegaconf import OmegaConf, open_dict

## Downloading the config file of conformer ctc

In [2]:
BRANCH = 'r1.23.0'
!mkdir configs
!wget -P configs/ https://raw.githubusercontent.com/NVIDIA/NeMo/main/examples/asr/conf/conformer/conformer_ctc_bpe.yaml

--2024-04-27 22:59:18--  https://raw.githubusercontent.com/NVIDIA/NeMo/main/examples/asr/conf/conformer/conformer_ctc_bpe.yaml
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.110.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 10228 (10.0K) [text/plain]
Saving to: ‘configs/conformer_ctc_bpe.yaml’

conformer_ctc_bpe.y 100%[===================>]   9.99K  --.-KB/s    in 0.002s  

2024-04-27 22:59:19 (3.99 MB/s) - ‘configs/conformer_ctc_bpe.yaml’ saved [10228/10228]



## Downloading and processing the NeMo Tokenizer Script

In [ ]:
# Downloading the tokenizer
if not os.path.exists("scripts/tokenizers/process_asr_text_tokenizer.py"):
  !mkdir scripts
  !wget -P scripts/ https://raw.githubusercontent.com/NVIDIA/NeMo/$BRANCH/scripts/tokenizers/process_asr_text_tokenizer.py

### Training the tokenizer

In [ ]:
# Training our tokenizer
!python ./scripts/process_asr_text_tokenizer.py \
  --manifest="train.json" \
  --data_root="./" \
  --vocab_size=1024 \
  --tokenizer="spe" \
  --spe_type="unigram" \
  --log

In [3]:
# taking a look on our vocab
!head -n 20 tokenizer_spe_unigram_v1024/vocab.txt

▁
##ا
##ه
##ت
##ي
##ن
##ة
ال
##م
##ك
من
و
ي
##ع
ت
##د
##ق
##ح
##ون
أ


In [4]:
# loading our cfg to edit it
params = OmegaConf.load("./configs/config_bpe.yaml")
print(OmegaConf.to_yaml(params))

name: ContextNet5x1
sample_rate: 16000
repeat: 1
dropout: 0.0
separable: true
model:
  train_ds:
    manifest_filepath: ???
    sample_rate: 16000
    batch_size: 32
    trim_silence: true
    max_duration: 16.7
    shuffle: true
    num_workers: 8
    pin_memory: true
    is_tarred: false
    tarred_audio_filepaths: null
    shard_strategy: scatter
    shuffle_n: 2048
    bucketing_strategy: synced_randomized
    bucketing_batch_size: null
  validation_ds:
    manifest_filepath: ???
    sample_rate: 16000
    batch_size: 32
    shuffle: false
    num_workers: 8
    pin_memory: true
  tokenizer:
    dir: ???
    type: ???
  preprocessor:
    _target_: nemo.collections.asr.modules.AudioToMelSpectrogramPreprocessor
    normalize: per_feature
    window_size: 0.02
    sample_rate: 16000
    window_stride: 0.01
    window: hann
    features: 64
    n_fft: 512
    frame_splicing: 1
    dither: 1.0e-05
  spec_augment:
    _target_: nemo.collections.asr.modules.SpectrogramAugmentation
    rec

In [5]:
# filling our datasets to the cfg file
params.model.train_ds.manifest_filepath = 'train.json'
params.model.validation_ds.manifest_filepath = 'dev.json'

## instantiate the model

In [6]:
conformer_ctc_small = nemo_asr.models.EncDecCTCModelBPE.from_pretrained(model_name="stt_en_conformer_ctc_small")
conformer_ctc_small.summarize()

[NeMo I 2024-04-28 01:56:44 cloud:58] Found existing object /home/mostafa/.cache/torch/NeMo/NeMo_1.23.0/stt_en_conformer_ctc_small/5d2d8e5b2b5adb8f5091363c6ba19c55/stt_en_conformer_ctc_small.nemo.
[NeMo I 2024-04-28 01:56:44 cloud:64] Re-using file from: /home/mostafa/.cache/torch/NeMo/NeMo_1.23.0/stt_en_conformer_ctc_small/5d2d8e5b2b5adb8f5091363c6ba19c55/stt_en_conformer_ctc_small.nemo
[NeMo I 2024-04-28 01:56:44 common:924] Instantiating model from pre-trained checkpoint


[NeMo I 2024-04-28 01:56:44 mixins:172] Tokenizer SentencePieceTokenizer initialized with 1024 tokens


[NeMo W 2024-04-28 01:56:45 modelPT:165] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    manifest_filepath: /data/NeMo_ASR_SET/English/v2.0/train/tarred_audio_manifest.json
    sample_rate: 16000
    batch_size: 64
    shuffle: true
    num_workers: 8
    pin_memory: true
    use_start_end_token: false
    trim_silence: false
    max_duration: 20.0
    min_duration: 0.1
    shuffle_n: 2048
    is_tarred: true
    tarred_audio_filepaths: /data/NeMo_ASR_SET/English/v2.0/train/audio__OP_0..4095_CL_.tar
    
[NeMo W 2024-04-28 01:56:45 modelPT:172] If you intend to do validation, please call the ModelPT.setup_validation_data() or ModelPT.setup_multiple_validation_data() method and provide a valid configuration file to setup the validation data loader(s). 
    Validation config : 
    manifest_filepath:
    - /data/ASR/LibriSpeech/librispeech_withs

[NeMo I 2024-04-28 01:56:45 features:289] PADDING: 0
[NeMo I 2024-04-28 01:56:46 save_restore_connector:249] Model EncDecCTCModelBPE was successfully restored from /home/mostafa/.cache/torch/NeMo/NeMo_1.23.0/stt_en_conformer_ctc_small/5d2d8e5b2b5adb8f5091363c6ba19c55/stt_en_conformer_ctc_small.nemo.


  | Name              | Type                              | Params
------------------------------------------------------------------------
0 | preprocessor      | AudioToMelSpectrogramPreprocessor | 0     
1 | encoder           | ConformerEncoder                  | 13.0 M
2 | decoder           | ConvASRDecoder                    | 181 K 
3 | loss              | CTCLoss                           | 0     
4 | spec_augmentation | SpectrogramAugmentation           | 0     
5 | wer               | WER                               | 0     
------------------------------------------------------------------------
13.2 M    Trainable params
0         Non-trainable params
13.2 M    Total params
52.616    Total estimated model params size (MB)

In [7]:
# Changing the default tokenizer
conformer_ctc_small.change_vocabulary(
    new_tokenizer_dir='tokenizer_spe_unigram_v1024',
    new_tokenizer_type="bpe"
)
# Point to the data we'll use for fine-tuning as the training and validation set
conformer_ctc_small.setup_training_data(train_data_config=params['model']['train_ds'])
conformer_ctc_small.setup_validation_data(val_data_config=params['model']['validation_ds'])


[NeMo W 2024-04-28 01:56:47 modelPT:258] You tried to register an artifact under config key=tokenizer.model_path but an artifact for it has already been registered.
[NeMo W 2024-04-28 01:56:47 modelPT:258] You tried to register an artifact under config key=tokenizer.vocab_path but an artifact for it has already been registered.
[NeMo W 2024-04-28 01:56:47 modelPT:258] You tried to register an artifact under config key=tokenizer.spe_tokenizer_vocab but an artifact for it has already been registered.


[NeMo I 2024-04-28 01:56:47 mixins:172] Tokenizer SentencePieceTokenizer initialized with 1024 tokens
[NeMo I 2024-04-28 01:56:47 ctc_bpe_models:248] 
    Replacing old number of classes (1024) with new number of classes - 1024
[NeMo I 2024-04-28 01:56:47 ctc_bpe_models:290] Changed tokenizer to ['<unk>', '▁', 'ا', 'ه', 'ت', 'ي', 'ن', 'ة', '▁ال', 'م', 'ك', '▁من', '▁و', '▁ي', 'ع', '▁ت', 'د', 'ق', 'ح', 'ون', '▁أ', '▁في', 'ل', 'وا', '▁م', 'ى', 'ب', 'ر', '▁ب', '▁أن', 'ين', 'ف', 'هم', 'س', 'نا', 'و', 'ط', '▁لا', '▁الم', 'ها', '▁الله', 'ص', '▁ما', '▁ل', 'ش', '▁ف', 'ج', '▁إن', '▁سامي', 'على', 'ز', '▁إل', '▁كان', '▁ن', 'ض', 'خ', 'ما', 'أ', 'اء', 'ئ', 'ني', 'كم', '▁لم', '▁بال', 'ث', 'ذ', 'ان', '▁وال', 'غ', '▁عن', '▁ع', '▁الأ', 'ية', '▁الذي', 'را', 'ول', 'ات', '▁هذا', '▁كل', '▁هل', 'اب', '▁قال', 'ار', 'ظ', 'ال', '▁س', '▁لل', '▁مع', '▁ولا', '▁هو', 'ور', 'ته', '▁وأ', '▁ذلك', 'ري', '▁ح', 'صل', 'لا', '▁إ', '▁ش', 'دي', '▁توم', '▁أنا', 'رب', 'عد', 'ير', 'اد', '▁وما', '▁يوم', '▁أم', '▁إلا', '▁الح', '▁خ

In [8]:
# Setting up our trainer
trainer = pl.Trainer(devices=1, accelerator='gpu', max_epochs=60, default_root_dir="checkpoints")
#Start training!!!
trainer.fit(conformer_ctc_small)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


[NeMo I 2024-04-28 01:56:51 modelPT:723] Optimizer config = AdamW (
    Parameter Group 0
        amsgrad: False
        betas: [0.9, 0.98]
        capturable: False
        differentiable: False
        eps: 1e-08
        foreach: None
        fused: None
        lr: 2.0
        maximize: False
        weight_decay: 0
    )
[NeMo I 2024-04-28 01:56:51 lr_scheduler:915] Scheduler "<nemo.core.optim.lr_scheduler.NoamAnnealing object at 0x7ff011384e20>" 
    will be used during training (effective maximum steps = 53220) - 
    Parameters : 
    (d_model: 176
    warmup_steps: 10000
    warmup_ratio: null
    min_lr: 1.0e-06
    max_steps: 53220
    )



  | Name              | Type                              | Params
------------------------------------------------------------------------
0 | preprocessor      | AudioToMelSpectrogramPreprocessor | 0     
1 | encoder           | ConformerEncoder                  | 13.0 M
2 | spec_augmentation | SpectrogramAugmentation           | 0     
3 | wer               | WER                               | 0     
4 | decoder           | ConvASRDecoder                    | 181 K 
5 | loss              | CTCLoss                           | 0     
------------------------------------------------------------------------
13.2 M    Trainable params
0         Non-trainable params
13.2 M    Total params
52.616    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

[NeMo I 2024-04-28 01:56:53 wer:318] 
    
[NeMo I 2024-04-28 01:56:53 wer:319] reference:هو يقرأ كتابا
[NeMo I 2024-04-28 01:56:53 wer:320] predicted:لمنذنب المأنزلناصاحب قلرسل عليكمذنبلالم متأكد وهذاوق فاستعدك كلعد الشيطاناللهلكجروق لمن فيها
[NeMo I 2024-04-28 01:56:53 wer:318] 
    
[NeMo I 2024-04-28 01:56:53 wer:319] reference:ما أبلغ العظات قال
[NeMo I 2024-04-28 01:56:53 wer:320] predicted:لمنجر الم يأكل الاست قولاختلافرسل مراء إذا كريمشعرستطيع ال نطف ويومزلظالمطاعونريجر ولكن الاست أت تعرف أت لاطاع لا يا عظيم مزيدالجبالجر لمنختلف لمن فيها


...

Validation: 0it [00:00, ?it/s]

[NeMo I 2024-04-29 00:43:17 wer:318] 
    
[NeMo I 2024-04-29 00:43:17 wer:319] reference:هو يقرأ كتابا
[NeMo I 2024-04-29 00:43:17 wer:320] predicted:هو يقرأ كتابا
[NeMo I 2024-04-29 00:43:18 wer:318] 
    
[NeMo I 2024-04-29 00:43:18 wer:319] reference:ما أبلغ العظات قال
[NeMo I 2024-04-29 00:43:18 wer:320] predicted:ما أبلغ العظات قال
[NeMo I 2024-04-29 00:43:18 wer:318] 
    
[NeMo I 2024-04-29 00:43:18 wer:319] reference:لقد انهارت حياة ليلى
[NeMo I 2024-04-29 00:43:18 wer:320] predicted:لقد إنعت حياة ليلى
[NeMo I 2024-04-29 00:43:19 wer:318] 
    
[NeMo I 2024-04-29 00:43:19 wer:319] reference:إن تقرب من النار تشعر بحرارتها
[NeMo I 2024-04-29 00:43:19 wer:320] predicted:انت تقترب من النار تصعب بحراراتها
[NeMo I 2024-04-29 00:43:19 wer:318] 
    
[NeMo I 2024-04-29 00:43:19 wer:319] reference:عيناي تؤلمانني
[NeMo I 2024-04-29 00:43:19 wer:320] predicted:عينت إواني
[NeMo I 2024-04-29 00:43:20 wer:318] 
    
[NeMo I 2024-04-29 00:43:20 wer:319] reference:أخبرني من فضلك إلى أي مكان أ

Validation: 0it [00:00, ?it/s]

[NeMo I 2024-04-29 01:10:44 wer:318] 
    
[NeMo I 2024-04-29 01:10:44 wer:319] reference:هو يقرأ كتابا
[NeMo I 2024-04-29 01:10:44 wer:320] predicted:هو يقرأ كتابا
[NeMo I 2024-04-29 01:10:47 wer:318] 
    
[NeMo I 2024-04-29 01:10:47 wer:319] reference:ما أبلغ العظات قال
[NeMo I 2024-04-29 01:10:47 wer:320] predicted:ما أبلغ العظات قال
[NeMo I 2024-04-29 01:10:49 wer:318] 
    
[NeMo I 2024-04-29 01:10:49 wer:319] reference:لقد انهارت حياة ليلى
[NeMo I 2024-04-29 01:10:49 wer:320] predicted:لقد إنعت حياة ليلى
[NeMo I 2024-04-29 01:10:51 wer:318] 
    
[NeMo I 2024-04-29 01:10:51 wer:319] reference:إن تقرب من النار تشعر بحرارتها
[NeMo I 2024-04-29 01:10:51 wer:320] predicted:انتقتب من النار تصعب بحراراتها
[NeMo I 2024-04-29 01:10:52 wer:318] 
    
[NeMo I 2024-04-29 01:10:52 wer:319] reference:عيناي تؤلمانني
[NeMo I 2024-04-29 01:10:52 wer:320] predicted:عينس إواني
[NeMo I 2024-04-29 01:10:52 wer:318] 
    
[NeMo I 2024-04-29 01:10:52 wer:319] reference:أخبرني من فضلك إلى أي مكان أذهب

`Trainer.fit` stopped: `max_epochs=60` reached.


## Launching Tensorboard

In [ ]:
%reload_ext tensorboard
%tensorboard --logdir=checkpoints/lightning_logs/

## Save the model

In [9]:
conformer_ctc_small.save_to("conformer_ctc_small_60e_adamw_32wv.nemo")

## Evaluate the model with the test set

In [10]:
params.model.validation_ds.manifest_filepath = "test.json"
# Bigger batch-size = bigger throughput
#params['model']['test_ds']['batch_size'] = 16

# Setup the test data loader and make sure the model is on GPU
conformer_ctc_small.setup_test_data(test_data_config=params['model']['validation_ds'])
conformer_ctc_small.cuda()
conformer_ctc_small.eval()

# We remove some preprocessing artifacts which benefit training
conformer_ctc_small.preprocessor.featurizer.pad_to = 0
conformer_ctc_small.preprocessor.featurizer.dither = 0.0

# We will be computing Word Error Rate (WER) metric between our hypothesis and predictions.
# WER is computed as numerator/denominator.
# We'll gather all the test batches' numerators and denominators.
wer_nums = []
wer_denoms = []

# Loop over all test batches.
# Iterating over the model's `test_dataloader` will give us:
# (audio_signal, audio_signal_length, transcript_tokens, transcript_length)
# See the AudioToCharDataset for more details.
for test_batch in conformer_ctc_small.test_dataloader():
        test_batch = [x.cuda() for x in test_batch]
        targets = test_batch[2]
        targets_lengths = test_batch[3]        
        log_probs, encoded_len, greedy_predictions = conformer_ctc_small(
            input_signal=test_batch[0], input_signal_length=test_batch[1]
        )
        # Notice the model has a helper object to compute WER
        conformer_ctc_small.wer.update(greedy_predictions, None, targets, targets_lengths)
        _, wer_num, wer_denom = conformer_ctc_small.wer.compute()
        wer_nums.append(wer_num.detach().cpu().numpy())
        wer_denoms.append(wer_denom.detach().cpu().numpy())

# We need to sum all numerators and denominators first. Then divide.
print(f"WER = {sum(wer_nums)/sum(wer_denoms)}")

[NeMo I 2024-04-29 01:16:31 collections:196] Dataset loaded with 10480 files totalling 12.67 hours
[NeMo I 2024-04-29 01:16:31 collections:197] 0 files were filtered totalling 0.00 hours
[NeMo I 2024-04-29 01:16:32 wer:318] 
    
[NeMo I 2024-04-29 01:16:32 wer:319] reference:هو يحبها و هي تحبه أيضا
[NeMo I 2024-04-29 01:16:32 wer:320] predicted:هو يحبها وهي تحبه أيضا
[NeMo I 2024-04-29 01:16:33 wer:318] 
    
[NeMo I 2024-04-29 01:16:33 wer:319] reference:ألا لا مرحبا بفراق ليلى
[NeMo I 2024-04-29 01:16:33 wer:320] predicted:أنا م ب في مقلة
[NeMo I 2024-04-29 01:16:33 wer:318] 
    
[NeMo I 2024-04-29 01:16:33 wer:319] reference:كان موتها صدمة كبيرة بالنسبة لي
[NeMo I 2024-04-29 01:16:33 wer:320] predicted:كان موتها صدنمة كبيرة بالنسبةدي
[NeMo I 2024-04-29 01:16:34 wer:318] 
    
[NeMo I 2024-04-29 01:16:34 wer:319] reference:طوبى لمن رفض الفتاة وقد غدا
[NeMo I 2024-04-29 01:16:34 wer:320] predicted:طوطوبى لما رفض الفتاة وقد غداد
[NeMo I 2024-04-29 01:16:36 wer:318] 
    
[NeMo I 2024

In [24]:
print(conformer_ctc_small.transcribe(paths2audio_files=["wavs/common_voice_ar_24044733.mp3.wav" ,
                                                    "wavs/common_voice_ar_24044422.mp3.wav"]#,
                                 #batch_size=2
                                 ))

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

['وكانوا يصرون على الحنث العظيم', 'ربما يود الذين كفروا لو كانوا مسلمين']
